# ML Pipeline Preparation
Follow the instructions below to help you create your ML pipeline.
### 1. Import libraries and load data from database.
- Import Python libraries
- Load dataset from database with [`read_sql_table`](https://pandas.pydata.org/pandas-docs/stable/generated/pandas.read_sql_table.html)
- Define feature and target variables X and Y

In [1]:
# import libraries
import pandas as pd
import numpy as np
import sqlite3
import pickle
import nltk
nltk.download(['punkt', 'wordnet'])
from sklearn.pipeline import Pipeline
from sqlalchemy import create_engine
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from sklearn.datasets import make_multilabel_classification
from sklearn.multioutput import MultiOutputClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import confusion_matrix

[nltk_data] Downloading package punkt to C:\Users\Christine
[nltk_data]     Liou\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping tokenizers\punkt.zip.
[nltk_data] Downloading package wordnet to C:\Users\Christine
[nltk_data]     Liou\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping corpora\wordnet.zip.


In [2]:
# load data from database
engine = create_engine('sqlite:///InsertDatabaseName.db')
df = pd.read_sql('select * from ETLTable', engine)
df.head()
X = df['message'] 
Y = df.iloc[:,4:40]

### 2. Write a tokenization function to process your text data

In [3]:
def tokenize(text):
    tokens = word_tokenize(text)
    
    # initiate lemmatizer
    lemmatizer = WordNetLemmatizer()

    # iterate through each token
    clean_tokens = []
    for tok in tokens:
        
    # lemmatize, normalize case, and remove leading/trailing white space
        clean_tok = lemmatizer.lemmatize(tok).lower().strip()
        clean_tokens.append(clean_tok)

    return clean_tokens

#Test the function
for message in X:
    tokens = tokenize(message)
    print(message)
    print(tokens, '\n')

Weather update - a cold front from Cuba that could pass over Haiti
['weather', 'update', '-', 'a', 'cold', 'front', 'from', 'cuba', 'that', 'could', 'pas', 'over', 'haiti'] 

Is the Hurricane over or is it not over
['is', 'the', 'hurricane', 'over', 'or', 'is', 'it', 'not', 'over'] 

Looking for someone but no name
['looking', 'for', 'someone', 'but', 'no', 'name'] 

UN reports Leogane 80-90 destroyed. Only Hospital St. Croix functioning. Needs supplies desperately.
['un', 'report', 'leogane', '80-90', 'destroyed', '.', 'only', 'hospital', 'st.', 'croix', 'functioning', '.', 'needs', 'supply', 'desperately', '.'] 

says: west side of Haiti, rest of the country today and tonight
['say', ':', 'west', 'side', 'of', 'haiti', ',', 'rest', 'of', 'the', 'country', 'today', 'and', 'tonight'] 

Information about the National Palace-
['information', 'about', 'the', 'national', 'palace-'] 

Storm at sacred heart of jesus
['storm', 'at', 'sacred', 'heart', 'of', 'jesus'] 

Please, we need tents an

['their', 'is', 'alot', 'of', 'problem', ',', 'their', 'is', 'no', 'money', 'for', 'the', 'people'] 

We need help. We are a Seguineau road at the corner of nazon and bertholy. We really need water.
['we', 'need', 'help', '.', 'we', 'are', 'a', 'seguineau', 'road', 'at', 'the', 'corner', 'of', 'nazon', 'and', 'bertholy', '.', 'we', 'really', 'need', 'water', '.'] 

my friend i have heard nothing again. i have a lot of problems. what u give i'll take I am in Jeremi, i want u to help me
['my', 'friend', 'i', 'have', 'heard', 'nothing', 'again', '.', 'i', 'have', 'a', 'lot', 'of', 'problem', '.', 'what', 'u', 'give', 'i', "'ll", 'take', 'i', 'am', 'in', 'jeremi', ',', 'i', 'want', 'u', 'to', 'help', 'me'] 

Their is silence no bus 65. I hv no food, water and alot of other things. Please come
['their', 'is', 'silence', 'no', 'bus', '65', '.', 'i', 'hv', 'no', 'food', ',', 'water', 'and', 'alot', 'of', 'other', 'thing', '.', 'please', 'come'] 

We are more than 50 people sleeping on the str

['we', 'are', 'in', 'lespinas', ',', 'around', 'fort', 'jacques', 'area', '(', 'fermathe', ',', 'upper', 'petion-ville', ')', '.', 'our', 'house', 'wa', 'destroyed', 'with', 'everything', 'wi', 'own', '.', 'please', 'we', 'need', 'food', ',', 'thank', 'you', '.'] 

I live in Boyer in Crois des Missions. Since the catastrophe the population hasn't received anything from the distribution yet. I would like that the authorities - Incomplete
['i', 'live', 'in', 'boyer', 'in', 'crois', 'de', 'missions', '.', 'since', 'the', 'catastrophe', 'the', 'population', 'ha', "n't", 'received', 'anything', 'from', 'the', 'distribution', 'yet', '.', 'i', 'would', 'like', 'that', 'the', 'authority', '-', 'incomplete'] 

Have some type of way for us with out that we all are going to die hungry thank you.
['have', 'some', 'type', 'of', 'way', 'for', 'u', 'with', 'out', 'that', 'we', 'all', 'are', 'going', 'to', 'die', 'hungry', 'thank', 'you', '.'] 

Good Morning I am in Haiti : I need my father and godfat

Please send food. Thank you. I'm in the village of La Plaine
['please', 'send', 'food', '.', 'thank', 'you', '.', 'i', "'m", 'in', 'the', 'village', 'of', 'la', 'plaine'] 

I think you will do the necessary things for me. .. Note : call for details. .. incomplete request
['i', 'think', 'you', 'will', 'do', 'the', 'necessary', 'thing', 'for', 'me', '.', '..', 'note', ':', 'call', 'for', 'detail', '.', '..', 'incomplete', 'request'] 

I live in Gonaives. The wounded are dying. They can't have/don't have doctors.
['i', 'live', 'in', 'gonaives', '.', 'the', 'wounded', 'are', 'dying', '.', 'they', 'ca', "n't", 'have/do', "n't", 'have', 'doctor', '.'] 

We are an accountant and two engineers. Please help us to find work or some food.
['we', 'are', 'an', 'accountant', 'and', 'two', 'engineer', '.', 'please', 'help', 'u', 'to', 'find', 'work', 'or', 'some', 'food', '.'] 

I lost my mother and my father and other people who died. These people are very dear to me. For now, I am living with someo

['if', 'someone', 'do', 'not', 'have', 'access', 'to', 'internet', 'where', 'can', 'he', 'bring', 'his', 'cv'] 

I thank you very much for your help. I want you to know that I am not from Port-au-Prince. I am from the city Des Cayes. I will give you my resume? very..
['i', 'thank', 'you', 'very', 'much', 'for', 'your', 'help', '.', 'i', 'want', 'you', 'to', 'know', 'that', 'i', 'am', 'not', 'from', 'port-au-prince', '.', 'i', 'am', 'from', 'the', 'city', 'des', 'cayes', '.', 'i', 'will', 'give', 'you', 'my', 'resume', '?', 'very..'] 

Good Day, I am happy your desk accepted my message. I am a student, I would like to get a job, I am in misery
['good', 'day', ',', 'i', 'am', 'happy', 'your', 'desk', 'accepted', 'my', 'message', '.', 'i', 'am', 'a', 'student', ',', 'i', 'would', 'like', 'to', 'get', 'a', 'job', ',', 'i', 'am', 'in', 'misery'] 

We are near Savanne on the road to Jacmel. We need help we don't have food or water
['we', 'are', 'near', 'savanne', 'on', 'the', 'road', 'to', '

...

The boats were rescuing marooned villagers in central Samastipur and Beghusarai districts when the accidents took place, raising the death toll in the current spell of floods in Bihar to 77.
['the', 'boat', 'were', 'rescuing', 'marooned', 'villager', 'in', 'central', 'samastipur', 'and', 'beghusarai', 'district', 'when', 'the', 'accident', 'took', 'place', ',', 'raising', 'the', 'death', 'toll', 'in', 'the', 'current', 'spell', 'of', 'flood', 'in', 'bihar', 'to', '77', '.'] 

Russia, the European Union, the U.S., Turkey and Belarus have sent helicopters, planes, rescue units and life-saving equipment.
['russia', ',', 'the', 'european', 'union', ',', 'the', 'u.s.', ',', 'turkey', 'and', 'belarus', 'have', 'sent', 'helicopter', ',', 'plane', ',', 'rescue', 'unit', 'and', 'life-saving', 'equipment', '.'] 

Chad, as well as Nigeria, Sudan and the Central African Republic, had welcomed hundreds of thousands of refugees who had fled armed conflicts or terrorist threats.
['chad', ',', 'a', 'w

However the ANA has established a base camp below the crash site.
['however', 'the', 'ana', 'ha', 'established', 'a', 'base', 'camp', 'below', 'the', 'crash', 'site', '.'] 

A number of countries, including Turkey, have been mindful of the possible need to deploy troops in response to a US-led invasion of Iraq.
['a', 'number', 'of', 'country', ',', 'including', 'turkey', ',', 'have', 'been', 'mindful', 'of', 'the', 'possible', 'need', 'to', 'deploy', 'troop', 'in', 'response', 'to', 'a', 'us-led', 'invasion', 'of', 'iraq', '.'] 

Nearly 290,000 people around the country have been forced to seek shelter in relief camps, NDMA said in figures published on its website.
['nearly', '290,000', 'people', 'around', 'the', 'country', 'have', 'been', 'forced', 'to', 'seek', 'shelter', 'in', 'relief', 'camp', ',', 'ndma', 'said', 'in', 'figure', 'published', 'on', 'it', 'website', '.'] 

The majority of the funds will be used to equip medical staff on the ground with the medicines and supplies mos

It is hard to stay here; life is doubly difficult at the evacuation centre. Some of the protests turned violent, and according to local observers, the Chadian police force killed four people, two in Ndjamena and two others in Sahr. Dirty water, sick animals used for food and other unhealthy eating conditions are causing health issues in other parts of Prey Veng too, so MCC's response includes cleaning wells, distributing hygiene kits and training teachers at Angkearhdei about hygiene and sanitation practices. However, the two patients will not know about their illness for at least a week after they were suspected to have the deadly and contagious virus. Communication minister Issa Tchiroma Bakary did not elaborate on the nationality of the foreigners, who were among the more than 100 killed during an attempted cross-border raid at the weekend. In the short-term, CARE is providing medicine to combat diarrhea, cholera and other diseases; hygiene messages instructing villagers on what ste

The forth round of polio immunisation for 2001 went ahead at the end of September.
['the', 'forth', 'round', 'of', 'polio', 'immunisation', 'for', '2001', 'went', 'ahead', 'at', 'the', 'end', 'of', 'september', '.'] 

On October 30, UNHCR reported that 540 refugees entered the Killi Faizo staging site near the Chaman border crossing in Baluchistan Province.After the deadly raid six months ago, Bouba, his children and their companions trekked north in fear of the jihadists to the dusty, windswept Lake Chad basin in the far northeast of Nigeria and bordering on western Chad.
['on', 'october', '30', ',', 'unhcr', 'reported', 'that', '540', 'refugee', 'entered', 'the', 'killi', 'faizo', 'staging', 'site', 'near', 'the', 'chaman', 'border', 'crossing', 'in', 'baluchistan', 'province.after', 'the', 'deadly', 'raid', 'six', 'month', 'ago', ',', 'bouba', ',', 'his', 'child', 'and', 'their', 'companion', 'trekked', 'north', 'in', 'fear', 'of', 'the', 'jihadist', 'to', 'the', 'dusty', ',', 'wind

['extreme', 'water', 'shortage', 'caused', 'by', 'two', 'to', 'three', 'year', 'of', 'failed', 'rain', 'ha', 'killed', 'huge', 'number', 'of', 'farm', 'animal', 'and', 'severely', 'reduced', 'crop', 'production', '.'] 

Damages running into millions of dollars are being claimed by people allegedly assaulted while in custody after the secessionist attacks, the report said.
['damages', 'running', 'into', 'million', 'of', 'dollar', 'are', 'being', 'claimed', 'by', 'people', 'allegedly', 'assaulted', 'while', 'in', 'custody', 'after', 'the', 'secessionist', 'attack', ',', 'the', 'report', 'said', '.'] 

Boats were recalled to port, people evacuated and flights cancelled across south China on Friday as Typhoon Megi, possibly the strongest to hit China this year, neared.
['boats', 'were', 'recalled', 'to', 'port', ',', 'people', 'evacuated', 'and', 'flight', 'cancelled', 'across', 'south', 'china', 'on', 'friday', 'a', 'typhoon', 'megi', ',', 'possibly', 'the', 'strongest', 'to', 'hit', 'chi

### 3. Build a machine learning pipeline
This machine pipeline should take in the `message` column as input and output classification results on the other 36 categories in the dataset. You may find the [MultiOutputClassifier](http://scikit-learn.org/stable/modules/generated/sklearn.multioutput.MultiOutputClassifier.html) helpful for predicting multiple target variables.

In [4]:
pipeline = Pipeline([
        ('vect', CountVectorizer(tokenizer=tokenize)),
        ('tfidf', TfidfTransformer()),
        ('clf', MultiOutputClassifier(KNeighborsClassifier()))])

### 4. Train pipeline
- Split data into train and test sets
- Train pipeline

In [5]:
#print(np.array(X).shape,np.array(Y).shape)
X_train,X_test,Y_train,Y_test = train_test_split(X, Y)

pipeline.fit(X_train, Y_train)


Pipeline(memory=None,
         steps=[('vect',
                 CountVectorizer(analyzer='word', binary=False,
                                 decode_error='strict',
                                 dtype=<class 'numpy.int64'>, encoding='utf-8',
                                 input='content', lowercase=True, max_df=1.0,
                                 max_features=None, min_df=1,
                                 ngram_range=(1, 1), preprocessor=None,
                                 stop_words=None, strip_accents=None,
                                 token_pattern='(?u)\\b\\w\\w+\\b',
                                 tokenizer=<function tokenize at 0x000001DE31DECD90>,
                                 vocabulary=None)),
                ('tfidf',
                 TfidfTransformer(norm='l2', smooth_idf=True,
                                  sublinear_tf=False, use_idf=True)),
                ('clf',
                 MultiOutputClassifier(estimator=KNeighborsClassifier(algorithm='au

### 5. Test your model
Report the f1 score, precision and recall for each output category of the dataset. You can do this by iterating through the columns and calling sklearn's `classification_report` on each.

In [6]:
# predict on test data
y_pred = pipeline.predict(X_test)

### 6. Improve your model
Use grid search to find better parameters. 

In [12]:
parameters = {
        'features__text_pipeline__vect__ngram_range': ((1, 1), (1, 2)),
        'features__text_pipeline__vect__max_df': (0.5, 0.75, 1.0),
        'features__text_pipeline__vect__max_features': (None, 5000, 10000),
        'features__text_pipeline__tfidf__use_idf': (True, False),
        'clf__n_estimators': [50, 100, 200],
        'clf__min_samples_split': [2, 3, 4],
        'features__transformer_weights': (
            {'text_pipeline': 1, 'starting_verb': 0.5},
            {'text_pipeline': 0.5, 'starting_verb': 1},
            {'text_pipeline': 0.8, 'starting_verb': 1},
        )
    }

cv = GridSearchCV(pipeline, param_grid=parameters)

### 7. Test your model
Show the accuracy, precision, and recall of the tuned model.  

Since this project focuses on code quality, process, and  pipelines, there is no minimum performance metric needed to pass. However, make sure to fine tune your models for accuracy, precision and recall to make your project stand out - especially for your portfolio!

In [33]:
accuracy = (y_pred == Y_test).mean()

print("Accuracy:", accuracy)


Accuracy: related                   0.767303
request                   0.887395
offer                     0.996639
aid_related               0.699465
medical_help              0.912758
medical_products          0.942552
search_and_rescue         0.972956
security                  0.982124
military                  0.969595
child_alone               1.000000
water                     0.934301
food                      0.894729
shelter                   0.903743
clothing                  0.985027
money                     0.976623
missing_people            0.988846
refugees                  0.964248
death                     0.945302
other_aid                 0.855462
infrastructure_related    0.929717
transport                 0.959817
buildings                 0.942704
electricity               0.980901
tools                     0.993888
hospitals                 0.987777
shops                     0.994652
aid_centers               0.987777
other_infrastructure      0.955844
weather_re

In [ ]:
test_pred = model.predict(X_test) 

for i in range(len(category_names)): 
    print(category_names[i]) 
    print(classification_report(Y_test[category_names[i]], y_pred[:, i]))

### 8. Try improving your model further. Here are a few ideas:
* try other machine learning algorithms
* add other features besides the TF-IDF

### 9. Export your model as a pickle file

In [36]:
# save the model to disk
pkl_filename = "pickle_model.pkl"
with open(pkl_filename, 'wb') as file:
    pickle.dump(pipeline, file)
 


### 10. Use this notebook to complete `train.py`
Use the template file attached in the Resources folder to write a script that runs the steps above to create a database and export a model based on a new dataset specified by the user.